***

# Data wrangling part

* https://towardsdatascience.com/how-to-create-a-plotly-visualization-and-embed-it-on-websites-517c1a78568b

***

In [1]:
# import os
# corpus_path = 'P:/My documents/Corona project/collected data/Work 2'
# os.chdir(corpus_path)

In [2]:
# # docx to txt using docx module # https://stackoverflow.com/questions/52719258/docx-file-to-text-file-conversion-using-python
# from docx import Document
# import io
# import shutil
# import os
# def convertDocxToText(path):
#     for d in os.listdir(path):
#         fileExtension=d.split(".")[-1]
#         if fileExtension =="docx":
#             docxFilename = path + d
#             document = Document(docxFilename)


#             textFilename = path + d.split(".")[0] + ".txt"
#             with io.open(textFilename,"w", encoding="utf-8") as textFile:
#                 for para in document.paragraphs: 
#                     textFile.write(str(para.text))
# path= path= "P:/My documents/Corona project/collected data/Work 2/"
# convertDocxToText(path)

In [3]:
# # Becare with this code, it removes all files with a given extension
# import glob
# removals = glob.glob('*.docx')
# for f in removals:
#     os.remove(f)

In [4]:
# # Write all the articles (stored as seperate .txt files) to one csv file 
# # https://stackoverflow.com/questions/41913147/combine-a-folder-of-text-files-into-a-csv-with-each-content-in-a-cell
# import csv
# from pathlib import Path
# with open('newspaper_articles_corona_20200922.csv', 'w', encoding='UTF-8', newline='') as out_file:
#     csv_out = csv.writer(out_file)
#     csv_out.writerow(['file', 'content'])
#     for fileName in Path('.').glob('*.txt'):
#         lines = [ ]
#         with open(str(fileName.absolute()),'rb') as one_text:
#             for line in one_text.readlines():
#                 lines.append(line.decode(encoding='UTF-8',errors='ignore').strip())
#         csv_out.writerow([str(fileName),' '.join(lines)])
# print("You now have a csv dataset, it is probably in the bottom of your working directory")

***

**Next time start with this code below**

***

In [5]:
# read as df
import os
corpus_path = 'P:/My documents/Corona project/collected data/Work 2'
os.chdir(corpus_path)
import pandas as pd
df = pd.read_csv("newspaper_articles_corona_20200922.csv", encoding='UTF-8')
df.reset_index(level=0, inplace=True)
print(df.shape)
df.head()

(19437, 3)


index                                               file  \
0      0         #coronahulp_ veel aanbod, weinig vraag.txt   
1      1  #VeiligAchterGlas_ Portretten in tijden van is...   
2      2  #VIRALEN Corona leidt tot andere liefdesverhal...   
3      3                                    (Geen) hond.txt   
4      4         (Nog niet) alle remmen los in de sport.txt   

                                             content  
0  De Volkskrant.nl14 maart 2020 zaterdag 03:07 P...  
1  de Volkskrant3 april 2020 vrijdag Copyright 20...  
2   NRC Handelsblad1 april 2020 woensdag, 1ste Ed...  
3  de Volkskrant18 maart 2020 woensdag Copyright ...  
4  de Volkskrant29 april 2020 woensdag Copyright ...

In [6]:
# Split to get body of article
df.dropna(inplace = True) 
df[['meta','body']] = df.content.str.split('Body', 1, expand=True)
df1 = df.copy()

In [7]:
df1.iloc[100]['body'] # row, collumn

'Utrecht - In de digitale reclame-vitrines in de binnenstad worden typisch  Utrechtse waarschuwingen tegen de verspreiding van het coronavirus vertoond.Die gaan van ’Hoesten, we have a problem’ naar ’Wees geen dakhaos maar een  thuisbaas!’ en ’Uuu kan dit!’. Deze ’coronaquotes’ zijn vervaardigd door de  stadsambassadeurs van Thirty030, die zich inzetten voor het merk Utrecht. De  quotes zijn verzameld na een oproep op Instagram en LinkedIn. Ook opgepikt  werden de quotes ’Binnen there, done that’ en ’Wie had dat gedacht? Van hangen  in de stad, naar thuis zitten op je gat’.ClassificationLanguage:\xa0DUTCH; NEDERLANDS  Publication-Type:\xa0Krant  Journal Code:\xa0telegraaf,Telegraph  Subject:\xa0Property + Housing Regulation + Policy (93%); Police Forces (93%); Internet Social Networking (90%); Arson (87%); Fires (71%); Communities + Neighborhoods (67%)  Industry:\xa0Residential Property (77%); Personal Care Services (69%); Internet + Www (64%); Personal Computers (63%)  Load-Date:\xa0A

In [8]:
# And split again to cut away the end of the text
df1[['body','rest']] = df1.body.str.split("Load-Date:",expand=True)
df1[['body','rest_2']] = df1.body.str.split("Graphic",expand=True)
df1[['body','rest_3']] = df1.body.str.split("ClassificationLanguage:",expand=True)
df1['body'] = df1['body'].str.replace('VOLLEDIGE TEKST:', '')
df1['body'] = df1['body'].str.replace('ABSTRACT', '')
print(df1.shape)

(19437, 8)


In [9]:
# Drop duplicates based on 'body'
df1 = df1.drop_duplicates(subset='body')
print(df1.shape)
# 19437 -> 19187

(19187, 8)


In [10]:
# Drop the unwanted "CoronaFiles"
df1 = df1.drop(df1.loc[df1['file'].str.startswith('CoronaFiles')].index)
print(df1.shape)

(19187, 8)


In [11]:
df1.iloc[100]['body'] # row, collumn

'Utrecht - In de digitale reclame-vitrines in de binnenstad worden typisch  Utrechtse waarschuwingen tegen de verspreiding van het coronavirus vertoond.Die gaan van ’Hoesten, we have a problem’ naar ’Wees geen dakhaos maar een  thuisbaas!’ en ’Uuu kan dit!’. Deze ’coronaquotes’ zijn vervaardigd door de  stadsambassadeurs van Thirty030, die zich inzetten voor het merk Utrecht. De  quotes zijn verzameld na een oproep op Instagram en LinkedIn. Ook opgepikt  werden de quotes ’Binnen there, done that’ en ’Wie had dat gedacht? Van hangen  in de stad, naar thuis zitten op je gat’.'

In [12]:
# Newspaper and source
df1 = df1.assign(newspaper='')
df1.loc[df1['meta'].str.contains('Telegraaf'), 'newspaper'] = 'tele'
df1.loc[df1['meta'].str.contains('NRC Handelsblad'), 'newspaper'] = 'nrc'
df1.loc[df1['meta'].str.contains('Volkskrant'), 'newspaper'] = 'volk'
df1.head()

index                                               file  \
0      0         #coronahulp_ veel aanbod, weinig vraag.txt   
1      1  #VeiligAchterGlas_ Portretten in tijden van is...   
2      2  #VIRALEN Corona leidt tot andere liefdesverhal...   
3      3                                    (Geen) hond.txt   
4      4         (Nog niet) alle remmen los in de sport.txt   

                                             content  \
0  De Volkskrant.nl14 maart 2020 zaterdag 03:07 P...   
1  de Volkskrant3 april 2020 vrijdag Copyright 20...   
2   NRC Handelsblad1 april 2020 woensdag, 1ste Ed...   
3  de Volkskrant18 maart 2020 woensdag Copyright ...   
4  de Volkskrant29 april 2020 woensdag Copyright ...   

                                                meta  \
0  De Volkskrant.nl14 maart 2020 zaterdag 03:07 P...   
1  de Volkskrant3 april 2020 vrijdag Copyright 20...   
2   NRC Handelsblad1 april 2020 woensdag, 1ste Ed...   
3  de Volkskrant18 maart 2020 woensdag Copyright ...   
4  de Volkskrant29 april 2020 woensdag Copyright ...   

                                                body  \
0    Onder de hashtag wordt ouderen en zieken hul...   
1  De Maastrichtse fotograaf Tetsuro Miyazaki is ...   
2  In tijden van isolatie worden lezer en schrijv...   
3  Column in AmersfoortDe labradoodle geldt al ja...   
4  Over de vierhonderd jeugdleden die weer bij zi...   

                              rest  \
0   March 14, 2020 End of Document   
1    April 2, 2020 End of Document   
2    April 1, 2020 End of Document   
3   March 17, 2020 End of Document   
4   April 28, 2020 End of Document   

                                              rest_2  \
0                                               None   
1   Familie Van StiphoutFamilie PowellFamilie Hei...   
2                                               None   
3   Een schatje of Frankenstein?De 'meisjes' van ...   
4   Medewerker Tim Stoevelaar plakt bij Rotterdam...   

                                              rest_3 newspaper  
0                                               None      volk  
1                                               None      volk  
2   DUTCH; NEDERLANDS  Publication-Type: Krant  S...       nrc  
3                                               None      volk  
4                                               None      volk

In [13]:
df1['date'] = df1['meta'].str.extract('(\d+\s\w+\s\d{4})', expand=True)

In [14]:
df1.iloc[3]['date']

'18 maart 2020'

In [15]:
# Clean date in column 'date'
df1['date'] = df1['date'].str.replace('^1\s', '01/')
df1['date'] = df1['date'].str.replace('^2\s', '02/')
df1['date'] = df1['date'].str.replace('^3\s', '03/')
df1['date'] = df1['date'].str.replace('^4\s', '04/')
df1['date'] = df1['date'].str.replace('^5\s', '05/')
df1['date'] = df1['date'].str.replace('^6\s', '06/')
df1['date'] = df1['date'].str.replace('^7\s', '07/')
df1['date'] = df1['date'].str.replace('^8\s', '08/')
df1['date'] = df1['date'].str.replace('^9\s', '09/')
df1['date'] = df1['date'].str.replace('januari', '01/')
df1['date'] = df1['date'].str.replace('februari', '02/')
df1['date'] = df1['date'].str.replace('maart', '03/')
df1['date'] = df1['date'].str.replace('april', '04/')
df1['date'] = df1['date'].str.replace('mei', '05/')
df1['date'] = df1['date'].str.replace('juni', '06/')
df1['date'] = df1['date'].str.replace('juli', '07/')
df1['date'] = df1['date'].str.replace('augustus', '08/')
df1['date'] = df1['date'].str.replace('september', '09/')
df1['date'] = df1['date'].str.replace('october', '10/')
df1['date'] = df1['date'].str.replace('november', '11/')
df1['date'] = df1['date'].str.replace('december', '12/')
df1['date'] = df1['date'].str.replace('(?<=\d{2})\s', '/') # negative lookbehind
df1['date'] = df1['date'].str.replace('\s', '')

In [16]:
df1.iloc[3]['date'] # row, collumn

'18/03/2020'

In [17]:
# convert string to date
df1['datetime']  = pd.to_datetime(df1['date'], format='%d/%m/%Y')
# Add a count (later useful for graphing)
df1['count'] = 1

In [18]:
# Create Plotly date = normal date + 1 day (due to bug in plotly)
# df1['datetime_pl'] = pd.DatetimeIndex(df1.datetime) + pd.DateOffset(1)
# print(df1.iloc[1]['date'])
# print(df1.iloc[1]['datetime'])

In [19]:
# Optional: save as xlsx
path = 'P:/My documents/Corona project/'
os.chdir(path)
df1.to_excel("corona_dataframe.xlsx")

In [20]:
# Optional: save as csv
path = 'P:/My documents/Corona project/'
os.chdir(path)
df1.to_csv('corona_dataframe.csv', sep='\t', encoding='utf-8')

***

### Data frames per source

***

In [21]:
df_tele = df1.copy()
df_tele.drop(df_tele.loc[df_tele['newspaper']!='tele'].index, inplace=True)
print(df_tele.shape)
df_tele.head()

(7981, 12)


index                                            file  \
34     34             _22 als een symbool voor bloei_.txt   
35     35                     _40 dagen_ tegen corona.txt   
36     36                _Adviezen opvolgen noodzaak_.txt   
37     37  _Afbreken seizoen is zonde voor Feyenoord_.txt   
38     38               _Alle inzet op zorg aan huis_.txt   

                                              content  \
34  De Telegraaf14 april 2020 dinsdag, Gehele Opla...   
35  De Telegraaf24 maart 2020 dinsdag, Gehele Opla...   
36  De Telegraaf14 maart 2020 zaterdag, Gehele Opl...   
37  De Telegraaf6 april 2020 maandag, Gehele Oplag...   
38  De Telegraaf18 april 2020 zaterdag, Gehele Opl...   

                                                 meta  \
34  De Telegraaf14 april 2020 dinsdag, Gehele Opla...   
35  De Telegraaf24 maart 2020 dinsdag, Gehele Opla...   
36  De Telegraaf14 maart 2020 zaterdag, Gehele Opl...   
37  De Telegraaf6 april 2020 maandag, Gehele Oplag...   
38  De Telegraaf18 april 2020 zaterdag, Gehele Opl...   

                                                 body  \
34  Nederlandse galeries zijn noodgedwongen extra ...   
35  Het woord quarantaine ligt op ieders lippen nu...   
36  door Arianne MantelAmsterdam - In Europa zijn ...   
37  ’Gio’ trots op ontwikkeling Bijlow en andere t...   
38  Nieuwe aanpak kabinet voor kwetsbare ouderendo...   

                               rest rest_2  \
34   April 13, 2020 End of Document   None   
35   March 23, 2020 End of Document   None   
36   March 14, 2020 End of Document   None   
37    April 5, 2020 End of Document   None   
38   April 17, 2020 End of Document   None   

                                               rest_3 newspaper        date  \
34   DUTCH; NEDERLANDS  Publication-Type: Krant  J...      tele  14/04/2020   
35   DUTCH; NEDERLANDS  Publication-Type: Krant  J...      tele  24/03/2020   
36                                               None      tele  14/03/2020   
37   DUTCH; NEDERLANDS  Publication-Type: Krant  J...      tele  06/04/2020   
38   DUTCH; NEDERLANDS  Publication-Type: Krant  J...      tele  18/04/2020   

     datetime  count  
34 2020-04-14      1  
35 2020-03-24      1  
36 2020-03-14      1  
37 2020-04-06      1  
38 2020-04-18      1

In [22]:
df_nrc = df1.copy()
df_nrc.drop(df_nrc.loc[df_nrc['newspaper']!='nrc'].index, inplace=True)
print(df_nrc.shape)
df_nrc.head()

(5456, 12)


index                                               file  \
2        2  #VIRALEN Corona leidt tot andere liefdesverhal...   
33      33               __n week was het restaurant open.txt   
539    539  1,5 meter_ Lastig, voor deblinde Jan ;De Flat.txt   
542    542                                              2.txt   
544    544                                            3,5.txt   

                                               content  \
2     NRC Handelsblad1 april 2020 woensdag, 1ste Ed...   
33   NRC Handelsblad11 april 2020 zaterdag, 1ste Ed...   
539   NRC Handelsblad14 april 2020 dinsdag, 1ste Ed...   
542  NRC Handelsblad7 augustus 2020 vrijdag, 1ste E...   
544  NRC Handelsblad17 maart 2020 dinsdag, 1ste Edi...   

                                                  meta  \
2     NRC Handelsblad1 april 2020 woensdag, 1ste Ed...   
33   NRC Handelsblad11 april 2020 zaterdag, 1ste Ed...   
539   NRC Handelsblad14 april 2020 dinsdag, 1ste Ed...   
542  NRC Handelsblad7 augustus 2020 vrijdag, 1ste E...   
544  NRC Handelsblad17 maart 2020 dinsdag, 1ste Edi...   

                                                  body  \
2    In tijden van isolatie worden lezer en schrijv...   
33   Reportage           Gedwongen sluiting        ...   
539  Hoe beïnvloedt corona de levens in de L-flat i...   
542  Google heeft in april, mei en juni bijna 2.600...   
544  De ontwikkelingen rond het coronavirus zorgden...   

                                rest  \
2      April 1, 2020 End of Document   
33    April 10, 2020 End of Document   
539   April 14, 2020 End of Document   
542   August 7, 2020 End of Document   
544   March 17, 2020 End of Document   

                                                rest_2  \
2                                                 None   
33    Het is rustig in de Amsterdamse binnenstad. M...   
539                                               None   
542                                               None   
544                                               None   

                                                rest_3 newspaper        date  \
2     DUTCH; NEDERLANDS  Publication-Type: Krant  S...       nrc  01/04/2020   
33                                                None       nrc  11/04/2020   
539   DUTCH; NEDERLANDS  Publication-Type: Krant  S...       nrc  14/04/2020   
542   DUTCH; NEDERLANDS  Publication-Type: Krant  S...       nrc  07/08/2020   
544   DUTCH; NEDERLANDS  Publication-Type: Krant  I...       nrc  17/03/2020   

      datetime  count  
2   2020-04-01      1  
33  2020-04-11      1  
539 2020-04-14      1  
542 2020-08-07      1  
544 2020-03-17      1

In [23]:
df_volk = df1.copy()
df_volk.drop(df_volk.loc[df_volk['newspaper']!='volk'].index, inplace=True)
print(df_volk.shape)
df_volk.head()

(5749, 12)


index                                               file  \
0      0         #coronahulp_ veel aanbod, weinig vraag.txt   
1      1  #VeiligAchterGlas_ Portretten in tijden van is...   
3      3                                    (Geen) hond.txt   
4      4         (Nog niet) alle remmen los in de sport.txt   
5      5  [50 DUIZEND mensen zijn wereldwijd bezweken aa...   

                                             content  \
0  De Volkskrant.nl14 maart 2020 zaterdag 03:07 P...   
1  de Volkskrant3 april 2020 vrijdag Copyright 20...   
3  de Volkskrant18 maart 2020 woensdag Copyright ...   
4  de Volkskrant29 april 2020 woensdag Copyright ...   
5  de Volkskrant3 april 2020 vrijdag Copyright 20...   

                                                meta  \
0  De Volkskrant.nl14 maart 2020 zaterdag 03:07 P...   
1  de Volkskrant3 april 2020 vrijdag Copyright 20...   
3  de Volkskrant18 maart 2020 woensdag Copyright ...   
4  de Volkskrant29 april 2020 woensdag Copyright ...   
5  de Volkskrant3 april 2020 vrijdag Copyright 20...   

                                                body  \
0    Onder de hashtag wordt ouderen en zieken hul...   
1  De Maastrichtse fotograaf Tetsuro Miyazaki is ...   
3  Column in AmersfoortDe labradoodle geldt al ja...   
4  Over de vierhonderd jeugdleden die weer bij zi...   
5  50 DUIZENDmensen zijn wereldwijd bezweken aan ...   

                              rest  \
0   March 14, 2020 End of Document   
1    April 2, 2020 End of Document   
3   March 17, 2020 End of Document   
4   April 28, 2020 End of Document   
5    April 2, 2020 End of Document   

                                              rest_2  \
0                                               None   
1   Familie Van StiphoutFamilie PowellFamilie Hei...   
3   Een schatje of Frankenstein?De 'meisjes' van ...   
4   Medewerker Tim Stoevelaar plakt bij Rotterdam...   
5                                               None   

                                              rest_3 newspaper        date  \
0                                               None      volk  14/03/2020   
1                                               None      volk  03/04/2020   
3                                               None      volk  18/03/2020   
4                                               None      volk  29/04/2020   
5   DUTCH; NEDERLANDS  Publication-Type: Krant  S...      volk  03/04/2020   

    datetime  count  
0 2020-03-14      1  
1 2020-04-03      1  
3 2020-03-18      1  
4 2020-04-29      1  
5 2020-04-03      1

In [24]:
# Article frequencies by year, month, or day (i.e. A-DEC, M, D)
# Tele
df_tele_1 = df_tele.set_index('datetime').resample('W')['count'].sum()
df_tele_1 = df_tele_1.reset_index()
# nrc
df_nrc_1 = df_nrc.set_index('datetime').resample('W')['count'].sum()
df_nrc_1 = df_nrc_1.reset_index()
# Volk
df_volk_1 = df_volk.set_index('datetime').resample('W')['count'].sum()
df_volk_1 = df_volk_1.reset_index()

In [25]:
# Graph
df_melt1 = df_tele_1.melt(id_vars='datetime', value_vars=['count'])
df_melt2 = df_nrc_1.melt(id_vars='datetime', value_vars=['count'])
df_melt3 = df_volk_1.melt(id_vars='datetime', value_vars=['count'])



import plotly.graph_objects as go
fig = go.Figure()


# Create and style traces
fig.add_trace(go.Scatter(x=df_melt1['datetime'], y=df_melt1['value'], name='Telegraaf',
                         line=dict(color='#E1D89F', width=2)))

fig.add_trace(go.Scatter(x=df_melt2['datetime'], y=df_melt2['value'], name='NRC',
                         line=dict(color='#CD8B76', width=2)))

fig.add_trace(go.Scatter(x=df_melt3['datetime'], y=df_melt3['value'], name='Volkskrant',
                         line=dict(color='#C45BAA', width=2)))

# Edit the layout
fig.update_layout(title="Wekelijkse media aandacht voor COVID-19 (per krantentitel)",
                    showlegend=True,
                    xaxis_rangeslider_visible=True,
                   xaxis_title='Date',
                   yaxis_title='# articles',
                   paper_bgcolor='rgba(0,0,0,0)',
                   plot_bgcolor='rgba(0,0,0,0)')

fig.update_xaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')


fig.show() # 'svg' helps to share graph through nbviewer. If this is not necessary, it can be removed for a better interactive plot.


In [26]:
# Save graph 
import chart_studio
username = 'renswilderom' # your username
api_key = 'JQ0okV7QsrTwEJJfp7dp' # your api key - go to profile > settings > regenerate key
chart_studio.tools.set_credentials_file(username=username, api_key=api_key)

# Online file
import chart_studio.plotly as py
py.plot(fig, filename = 'Wekelijkse media aandacht voor COVID-19 (per krantentitel)', auto_open=True)

# Local html file
import plotly.io as pio
pio.write_html(fig, file='Wekelijkse media aandacht voor COVID-19 (per krantentitel)', auto_open=True)

***

# Analysis part


***

***

### Frequencies

***

**Total amount of articles**

In [27]:
# Total article frequencies by year, month, or day (i.e. A-DEC, M, D)
df2 = df1.set_index('datetime').resample('D')['count'].sum()
df2 = df2.reset_index()
print(df2.sum()) 
df2

count    19186
dtype: int64


datetime  count
0   2019-12-04      1
1   2019-12-05      0
2   2019-12-06      0
3   2019-12-07      0
4   2019-12-08      0
..         ...    ...
265 2020-08-25     88
266 2020-08-26     99
267 2020-08-27    103
268 2020-08-28    119
269 2020-08-29    143

[270 rows x 2 columns]

In [28]:
# Total volume of news
# https://plot.ly/python/line-charts/
df_melt = df2.melt(id_vars='datetime', value_vars=['count'])

import plotly.graph_objects as go
fig = go.Figure()


# Create and style traces
fig.add_trace(go.Scatter(x=df_melt['datetime'], y=df_melt['value'], name='Articles',
                         line=dict(color='lightgrey', width=2)))


# Edit the layout
fig.update_layout(title="Dagelijkse media aandacht voor COVID-19 (in totaal)",
                      showlegend=False,
                    xaxis_rangeslider_visible=True,
                   xaxis_title='Date',
                   yaxis_title='# articles',
                   paper_bgcolor='rgba(0,0,0,0)',
                   plot_bgcolor='rgba(0,0,0,0)')

fig.update_xaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')


fig.show() # 'svg' helps to share graph through nbviewer. If this is not necessary, it can be removed for a better interactive plot.


In [29]:
# Figure 
# import chart_studio
# username = 'renswilderom' # your username
# api_key = 'JQ0okV7QsrTwEJJfp7dp' # your api key - go to profile > settings > regenerate key
# chart_studio.tools.set_credentials_file(username=username, api_key=api_key)
# import chart_studio.plotly as py
# py.plot(fig, filename = 'Dutch news on COVID-19', auto_open=True)
# import plotly.io as pio
# pio.write_html(fig, file='Dutch news on COVID-19', auto_open=True)

***

## Analyzing particular term frequencies

***

In [30]:
# Term frequencies economie
df1['econ'] = df1['body'].str.count('economi*') # check for . in other datasets
df3 = df1.set_index('datetime').resample('D')['econ'].sum()
df3 = df3.reset_index()
print(df3.sum())
df3

econ    9681.0
dtype: float64


datetime  econ
0   2019-12-04   0.0
1   2019-12-05   0.0
2   2019-12-06   0.0
3   2019-12-07   0.0
4   2019-12-08   0.0
..         ...   ...
265 2020-08-25  27.0
266 2020-08-26  45.0
267 2020-08-27  22.0
268 2020-08-28  34.0
269 2020-08-29  91.0

[270 rows x 2 columns]

In [31]:
# Term frequencies gezin
df1['gezin'] = df1['body'].str.count('gezin*') # check for . in other datasets
df4 = df1.set_index('datetime').resample('D')['gezin'].sum()
df4 = df4.reset_index()
print(df4.sum())
df4

gezin    7926.0
dtype: float64


datetime  gezin
0   2019-12-04    0.0
1   2019-12-05    0.0
2   2019-12-06    0.0
3   2019-12-07    0.0
4   2019-12-08    0.0
..         ...    ...
265 2020-08-25   33.0
266 2020-08-26   38.0
267 2020-08-27   54.0
268 2020-08-28   30.0
269 2020-08-29   95.0

[270 rows x 2 columns]

In [32]:
# Term frequencies angst and variations
df1['angst'] = df1['body'].str.count('bang|onrust|angst|ongerust|vrees|bevreesd') # bezorgd en zorgen ambivalent
df5 = df1.set_index('datetime').resample('D')['angst'].sum()
df5 = df5.reset_index()
print(df5.sum())
df5

angst    8116.0
dtype: float64


datetime  angst
0   2019-12-04    0.0
1   2019-12-05    0.0
2   2019-12-06    0.0
3   2019-12-07    0.0
4   2019-12-08    0.0
..         ...    ...
265 2020-08-25   34.0
266 2020-08-26   33.0
267 2020-08-27   43.0
268 2020-08-28   49.0
269 2020-08-29   63.0

[270 rows x 2 columns]

In [33]:
# Term frequencies dood
df1['dood'] = df1['body'].str.count('doden|dood|overleden|gestorven') 
df6 = df1.set_index('datetime').resample('D')['dood'].sum()
df6 = df6.reset_index()
print(df6.sum())
df6

dood    8245.0
dtype: float64


datetime  dood
0   2019-12-04   0.0
1   2019-12-05   0.0
2   2019-12-06   0.0
3   2019-12-07   0.0
4   2019-12-08   0.0
..         ...   ...
265 2020-08-25  24.0
266 2020-08-26  18.0
267 2020-08-27  26.0
268 2020-08-28  27.0
269 2020-08-29  57.0

[270 rows x 2 columns]

In [34]:
# Term frequencies paniek
df1['paniek'] = df1['body'].str.count('paniek*') # check for . in other datasets
df7 = df1.set_index('datetime').resample('D')['paniek'].sum()
df7 = df7.reset_index()
print(df7.sum())
df7

paniek    1081.0
dtype: float64


datetime  paniek
0   2019-12-04     0.0
1   2019-12-05     0.0
2   2019-12-06     0.0
3   2019-12-07     0.0
4   2019-12-08     0.0
..         ...     ...
265 2020-08-25     3.0
266 2020-08-26     3.0
267 2020-08-27     2.0
268 2020-08-28     2.0
269 2020-08-29     2.0

[270 rows x 2 columns]

In [35]:
# Term frequencies paniek
df1['troost'] = df1['body'].str.count('troost*') # check for . in other datasets
df8 = df1.set_index('datetime').resample('W')['troost'].sum()
df8 = df8.reset_index()
print(df8.sum())
df8

troost    529.0
dtype: float64


datetime  troost
0  2019-12-08     0.0
1  2019-12-15     0.0
2  2019-12-22     0.0
3  2019-12-29     0.0
4  2020-01-05     0.0
5  2020-01-12     0.0
6  2020-01-19     0.0
7  2020-01-26     1.0
8  2020-02-02     1.0
9  2020-02-09     2.0
10 2020-02-16     0.0
11 2020-02-23     2.0
12 2020-03-01     9.0
13 2020-03-08     1.0
14 2020-03-15    12.0
15 2020-03-22    27.0
16 2020-03-29    43.0
17 2020-04-05    41.0
18 2020-04-12    31.0
19 2020-04-19    24.0
20 2020-04-26    35.0
21 2020-05-03    29.0
22 2020-05-10    30.0
23 2020-05-17    36.0
24 2020-05-24    23.0
25 2020-05-31    17.0
26 2020-06-07     7.0
27 2020-06-14    15.0
28 2020-06-21     9.0
29 2020-06-28    17.0
30 2020-07-05    15.0
31 2020-07-12    17.0
32 2020-07-19    21.0
33 2020-07-26     9.0
34 2020-08-02     6.0
35 2020-08-09    11.0
36 2020-08-16    10.0
37 2020-08-23     6.0
38 2020-08-30    22.0

In [36]:
# plot focus term
df_melt = df8.melt(id_vars='datetime', value_vars=['troost'])

import plotly.graph_objects as go
fig = go.Figure()


# Create and style traces
fig.add_trace(go.Scatter(x=df_melt['datetime'], y=df_melt['value'], name='References to term',
                         line=dict(color='aquamarine', width=2)))


# Edit the layout
fig.update_layout(title="References to certain term in Dutch news on COVID-19",
                      showlegend=False,
                    xaxis_rangeslider_visible=True,
                   xaxis_title='Date',
                   yaxis_title='# articles',
                   paper_bgcolor='rgba(0,0,0,0)',
                   plot_bgcolor='rgba(0,0,0,0)')

fig.update_xaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')


fig.show() # 'svg' helps to share graph through nbviewer. If this is not necessary, it can be removed for a better interactive plot.


In [37]:
# Merge data frames 
dfs = [df3, df4, df5, df6, df7]
from functools import reduce
df_temp = reduce(lambda  left,right: pd.merge(left,right,on=['datetime'],
                                            how='left'), dfs)
df_temp

datetime  econ  gezin  angst  dood  paniek
0   2019-12-04   0.0    0.0    0.0   0.0     0.0
1   2019-12-05   0.0    0.0    0.0   0.0     0.0
2   2019-12-06   0.0    0.0    0.0   0.0     0.0
3   2019-12-07   0.0    0.0    0.0   0.0     0.0
4   2019-12-08   0.0    0.0    0.0   0.0     0.0
..         ...   ...    ...    ...   ...     ...
265 2020-08-25  27.0   33.0   34.0  24.0     3.0
266 2020-08-26  45.0   38.0   33.0  18.0     3.0
267 2020-08-27  22.0   54.0   43.0  26.0     2.0
268 2020-08-28  34.0   30.0   49.0  27.0     2.0
269 2020-08-29  91.0   95.0   63.0  57.0     2.0

[270 rows x 6 columns]

In [38]:
# In df_temp replace 0 by Nan
import numpy as np
df_temp_nan = df_temp.copy()
df_temp_nan.replace(0, np.nan, inplace=True)
df_temp_nan.head()

datetime  econ  gezin  angst  dood  paniek
0 2019-12-04   NaN    NaN    NaN   NaN     NaN
1 2019-12-05   NaN    NaN    NaN   NaN     NaN
2 2019-12-06   NaN    NaN    NaN   NaN     NaN
3 2019-12-07   NaN    NaN    NaN   NaN     NaN
4 2019-12-08   NaN    NaN    NaN   NaN     NaN

In [39]:
# Angst, economy, hospital
# DUAL AXIS
# https://plot.ly/python/text-and-annotations/
import plotly.graph_objects as go
from plotly.subplots import make_subplots

x = df_temp['datetime']

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])


fig.add_trace(
    go.Scatter(x=x, y=df_temp_nan['angst'], name="Angst (& variations)", opacity=0.7, mode='markers', marker=dict(size=5, 
                color='springgreen')), secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_temp_nan['econ'], name="Economi*", opacity=0.7, mode='markers', marker=dict(size=5,
                color='lightslategrey')), secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_temp_nan['gezin'], name="Gezin*", opacity=0.7, mode='markers', marker=dict(size=5,
                color='lightsalmon')), secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_temp_nan['dood'], name="Dood (& variations)", opacity=0.7, mode='markers', marker=dict(size=5,
                color='orchid')), secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_temp_nan['paniek'], name="Paniek*", opacity=0.7, mode='markers', marker=dict(size=5,
                color='#004E89')), secondary_y=False)

fig.update_layout(showlegend=True,
    xaxis_rangeslider_visible=True,
    width=1200,
    height=600,
    title_text="Angst, economy, hospital, and dead",
    annotations=[
            dict(
            x="2020-02-27",
            y=0,         
            text="First corona patient in the Netherlands",
            ax=-90,
            ay=-250,
            opacity=0.7,
            arrowhead=7)])


fig.update_layout(paper_bgcolor='rgba(0,0,0,0)', plot_bgcolor='rgba(0,0,0,0)')
fig.update_xaxes(title_text="Date", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(title_text="# References to Angst", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(title_text="# References to Econony and hospital", showgrid=False, secondary_y=True)
fig.show()

In [40]:
# # Save figure
# import chart_studio
# username = 'renswilderom' # your username
# api_key = 'JQ0okV7QsrTwEJJfp7dp' # your api key - go to profile > settings > regenerate key
# chart_studio.tools.set_credentials_file(username=username, api_key=api_key)
# import chart_studio.plotly as py
# py.plot(fig, filename = 'Family, economie, angst, and dead', auto_open=True)
# import plotly.io as pio
# pio.write_html(fig, file='Family, economie, angst, and dead', auto_open=True)

***

## Topic modeling


***

In [41]:
# Import necessary packages and such
from __future__ import print_function
import pyLDAvis
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

import warnings
warnings.filterwarnings('ignore') # only use this when you know the script and want to supress unnecessary warnings

In [42]:
# Stop word source: https://raw.githubusercontent.com/stopwords-iso/stopwords-nl/master/stopwords-nl.txt
# toegevoegd "zegt"
dutch_stopwords = [
 "aan", "aangaande","aangezien", "achte", 
"achter", "achterna", "af", "afgelopen", "al", "aldaar", 
"aldus", "alhoewel", "alias", "alle", "allebei", "alleen", 
"alles", "als", "alsnog", "altijd", "altoos", "ander", "andere", 
"anders", "anderszins", "beetje", "behalve", "behoudens", "beide", 
"beiden", "ben", "beneden", "bent", "bepaald", "betreffende", 
"bij", "bijna", "bijv", "binnen", "binnenin", "blijkbaar", "blijken", 
"boven", "bovenal", "bovendien", "bovengenoemd", "bovenstaand", 
"bovenvermeld", "buiten", "bv", "daar", "daardoor", "daarheen", 
"daarin", "daarna", "daarnet", "daarom", "daarop", "daaruit", 
"daarvanlangs", "dan", "dat", "de", "deden", "deed", "der", "derde", 
"derhalve", "dertig", "deze", "dhr", "die", "dikwijls", "dit", 
"doch", "doe", "doen", "doet", "door", "doorgaand", "drie", 
"duizend", "dus", "echter", "een", "eens", "eer", "eerdat", 
"eerder", "eerlang", "eerst", "eerste", "eigen", "eigenlijk", 
"elk", "elke", "en", "enig", "enige", "enigszins", "enkel", "er", 
"erdoor", "erg", "ergens", "etc", "etcetera", "even", "eveneens", 
"evenwel", "gauw", "ge", "gedurende", "geen", "gehad", "gekund", 
"geleden", "gelijk", "gemoeten", "gemogen", "genoeg", "geweest", 
"gewoon", "gewoonweg", "haar", "haarzelf", "had", "hadden", "hare", 
"heb", "hebben", "hebt", "hedden", "heeft", "heel", "hem", "hemzelf", 
"hen", "het", "hetzelfde", "hier", "hierbeneden", "hierboven", "hierin", 
"hierna", "hierom", "hij", "hijzelf", "hoe", "hoewel", "honderd", "hun", 
"hunne", "ieder", "iedere", "iedereen", "iemand", "iets", "ik", "ikzelf", 
"in", "inderdaad", "inmiddels", "intussen", "inzake", "is", "ja", "je", 
"jezelf", "jij", "jijzelf", "jou", "jouw", "jouwe", "juist", "jullie", 
"kan", "klaar", "kon", "konden", "krachtens", "kun", "kunnen", "kunt", 
"laatst", "later", "liever", "lijken", "lijkt", "maak", "maakt", "maakte", 
"maakten", "maar", "mag", "maken", "me", "meer", "meest", "meestal", "men", 
"met", "mevr", "mezelf", "mij", "mijn", "mijnent", "mijner", "mijzelf", 
"minder", "miss", "misschien", "missen", "mits", "mocht", "mochten", 
"moest", "moesten", "moet", "moeten", "mogen", "mr", "mrs", "mw", "na", 
"naar", "nadat", "nam", "namelijk", "nee", "neem", "negen", "nemen", "nergens", 
"net", "niemand", "niet", "niets", "niks", "noch", "nochtans", "nog", "nogal", 
"nooit", "nu", "nv", "of", "ofschoon", "om", "omdat", "omhoog", "omlaag", 
"omstreeks", "omtrent", "omver", "ondanks", "onder", "ondertussen", "ongeveer", 
"ons", "onszelf", "onze", "onzeker", "ooit", "ook", "op", "opnieuw", "opzij", 
"over", "overal", "overeind", "overige", "overigens", "paar", "pas", "per", 
"precies", "recent", "redelijk", "reeds", "rond", "rondom", "samen", "sedert", 
"sinds", "sindsdien", "slechts", "sommige", "spoedig", "steeds", "tamelijk", 
"te", "tegen", "tegenover", "tenzij", "terwijl", "thans", "tien", "tiende", 
"tijdens", "tja", "toch", "toe", "toen", "toenmaals", "toenmalig", "tot", 
"totdat", "tussen", "twee", "tweede", "u", "uit", "uitgezonderd", "uw", 
"vaak", "vaakwat", "van", "vanaf", "vandaan", "vanuit", "vanwege", "veel", 
"veeleer", "veertig", "verder", "verscheidene", "verschillende", "vervolgens", 
"via", "vier", "vierde", "vijf", "vijfde", "vijftig", "vol", "volgend", "volgens", 
"voor", "vooraf", "vooral", "vooralsnog", "voorbij", "voordat", "voordezen", 
"voordien", "voorheen", "voorop", "voorts", "vooruit", "vrij", "vroeg", 
"waar", "waarom", "waarschijnlijk", "wanneer", "want", "waren", "was", 
"wat", "we", "wederom", "weer", "weg", "wegens", "weinig", "wel", 
"weldra", "welk", "welke", "werd", "werden", "werder", "wezen", 
"whatever", "wie", "wiens", "wier", "wij", "wijzelf", "wil", "wilden", 
"willen", "word", "worden", "wordt", "zal", "ze", "zei", "zegt" "zeker", 
"zelf", "zelfde", "zelfs", "zes", "zeven", "zich", "zichzelf", "zij", 
"zijn", "zijne", "zijzelf", "zo", "zoals", "zodat", "zodra", "zonder", 
"zou", "zouden", "zowat", "zulk", "zulke", "zullen", "zult"]

In [43]:
%%time
tf_vectorizer = CountVectorizer(lowercase = True,
                                         strip_accents = 'unicode',
                                         stop_words = dutch_stopwords,
                                         token_pattern = r'\b[a-zA-Z]{3,}\b', # keeps words of 3 or more characters
                                         max_df = 0.5, # ignore words occuring in > 50 % of the corpus (i.e. corpus specific stop words)
                                         min_df = 10) # ignore words in <10 documents of the corpus
dtm_tf = tf_vectorizer.fit_transform(df1['body'].values.astype('U')) # import articles from df 'content' as unicode string
print(dtm_tf.shape)

(19187, 33033)
Wall time: 52.4 s


**20 topic model**

In [44]:
# %%time
# # run the LDA model
# # TF DTM
# lda_tf_20 = LatentDirichletAllocation(n_components=20, random_state=0)
# lda_tf_20.fit(dtm_tf)

In [45]:
# # Conventional topics

# n_top_words = 30

# def print_top_words(model, feature_names, n_top_words):
#     for topic_idx, topic in enumerate(model.components_):
#         print("Topic #%d:" % topic_idx)
#         print(" ".join([feature_names[i]
#                         for i in topic.argsort()[:-n_top_words - 1:-1]]))
#     print()

# tf_feature_names = tf_vectorizer.get_feature_names() 
# print_top_words(lda_tf_20, tf_feature_names, n_top_words)

In [46]:
# %%time
# # LDA visualization
# pyLDAvis.sklearn.prepare(lda_tf_20, dtm_tf, tf_vectorizer)

**30-topic model**

In [47]:
%%time
# run the LDA model
# TF DTM
lda_tf_30 = LatentDirichletAllocation(n_components=30, random_state=0)
lda_tf_30.fit(dtm_tf)

Wall time: 4min 47s


LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='batch', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=30, n_jobs=None,
                          perp_tol=0.1, random_state=0, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [48]:
# Conventional topics

n_top_words = 30

def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        print("Topic #%d:" % topic_idx)
        print(" ".join([feature_names[i]
                        for i in topic.argsort()[:-n_top_words - 1:-1]]))
    print()

tf_feature_names = tf_vectorizer.get_feature_names() 
print_top_words(lda_tf_30, tf_feature_names, n_top_words)

Topic #0:
eten producten plastic leonard ilja klanten supermarkten vlees dag voedsel coronavirus pfeijffer plek kilo genua goed woont laat fruit impact schrijft rode week zegt winkel boodschappen restaurant groente hamsteren supermarkt
Topic #1:
patienten ziekenhuis zorg zegt ziekenhuizen artsen patient intensive corona coronapatienten care covid bedden gaat nodig gaan goed arts aantal komen ouderen leven verpleegkundigen komt hulp krijgen medische zien medisch behandeling
Topic #2:
dieren mens wereld natuur virus jaar corona aarde dier virussen nieuwe pandemie leven ziekte zien eeuw tijd wilde pest coronavirus zegt elkaar jaren soort grote vleermuizen vogels water griep onderzoek
Topic #3:
zegt gaan dag elkaar thuis gaat huis komen jaar kinderen zitten corona goed uur zit echt tijd zien komt mee week staan keer werk normaal vertelt staat afstand hele weken
Topic #4:
kinderen scholen school ouders onderwijs leerlingen studenten zegt gaan online gaat jongeren jaar leraren goed kind klas

In [49]:
%%time
# LDA visualization
pyLDAvis.sklearn.prepare(lda_tf_30, dtm_tf, tf_vectorizer)

Wall time: 14min 23s


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3      0.114146 -0.116292       1        1  11.178002
7      0.176447 -0.016157       2        1   8.914115
15     0.022071  0.018948       3        1   6.483708
20    -0.017925  0.027774       4        1   5.663167
14    -0.103208  0.006876       5        1   5.454937
9     -0.129371  0.084498       6        1   4.666207
12    -0.110337 -0.099675       7        1   4.612443
13    -0.070506 -0.043133       8        1   4.451039
23     0.074684  0.114674       9        1   3.964133
1     -0.046930 -0.105919      10        1   3.744666
6      0.064641  0.025136      11        1   3.576071
25     0.060726 -0.054964      12        1   3.326315
22    -0.143490  0.057537      13        1   3.111526
8     -0.098363  0.129395      14        1   3.097997
28    -0.025744 -0.140476      15        1   2.912487
18    -0.016541  0.130433      16        1   2.804291
21     0.168171  0.053211      17        1   2.496832
17     0.071959 -0.096534      18        1   2.388160
24    -0.079788 -0.009596      19        1   2.371120
2      0.027432  0.023006      20        1   2.021044
4     -0.013470 -0.142378      21        1   1.869794
19    -0.115541  0.023719      22        1   1.469727
10     0.203901  0.115371      23        1   1.442480
27    -0.124112  0.024727      24        1   1.363154
11     0.116308  0.025093      25        1   1.306805
0      0.097325 -0.106104      26        1   1.227238
26     0.005876 -0.074112      27        1   1.220563
16     0.001234  0.019742      28        1   1.177214
29     0.007029  0.169010      29        1   1.013494
5     -0.116625 -0.043810      30        1   0.671272, topic_info=      Category          Freq      Term         Total  loglift  logprob
13497  Default  24088.000000      jaar  24088.000000  30.0000  30.0000
30207  Default  11883.000000     virus  11883.000000  29.0000  29.0000
14328  Default   6851.000000  kinderen   6851.000000  28.0000  28.0000
21974  Default  10327.000000   procent  10327.000000  27.0000  27.0000
5125   Default   5625.000000     china   5625.000000  26.0000  26.0000
...        ...           ...       ...           ...      ...      ...
13497  Topic30    162.353126      jaar  24088.720093   0.0040  -5.2538
8914   Topic30    112.686268    franse   1639.309526   2.3263  -5.6189
25352  Topic30    134.246922     staat  10082.497136   0.6849  -5.4439
32586  Topic30    108.872710      ziek   2124.279869   2.0327  -5.6534
9052   Topic30    109.242465      gaat  17575.680028  -0.0770  -5.6500

[2498 rows x 6 columns], token_table=       Topic      Freq          Term
term                                
6          5  0.979245  aalderenrome
31        13  0.944828   aanbodschok
40         1  0.003634       aandeel
40         3  0.027258       aandeel
40         5  0.001817       aandeel
...      ...       ...           ...
33005      1  0.961437       zwerver
33032      1  0.016986           zzp
33032      3  0.007432           zzp
33032      8  0.777131           zzp
33032     13  0.197468           zzp

[14976 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 8, 16, 21, 15, 10, 13, 14, 24, 2, 7, 26, 23, 9, 29, 19, 22, 18, 25, 3, 5, 20, 11, 28, 12, 1, 27, 17, 30, 6])

**50-topic model**

In [50]:
%%time
# run the LDA model
# TF DTM
lda_tf_50 = LatentDirichletAllocation(n_components=50, random_state=0)
lda_tf_50.fit(dtm_tf)

Wall time: 5min 33s


LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='batch', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=50, n_jobs=None,
                          perp_tol=0.1, random_state=0, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)

In [51]:
# Conventional topics

n_top_words = 30

def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        print("Topic #%d:" % topic_idx)
        print(" ".join([feature_names[i]
                        for i in topic.argsort()[:-n_top_words - 1:-1]]))
    print()

tf_feature_names = tf_vectorizer.get_feature_names() 
print_top_words(lda_tf_50, tf_feature_names, n_top_words)

Topic #0:
eten producten supermarkten plastic goed klanten vlees dag restaurant winkels voedsel kilo fruit albert laat respondenten supermarkt vindt restaurants hamsteren thuis groente zegt heijn gaat bestellen eet rode koken boodschappen
Topic #1:
jongeren leven kinderen goed sociale onderzoek gaan gaat crisis houden ouderen zegt corona angst samenleving coronacrisis hoogleraar beter bijvoorbeeld tijd risico vraag virus zien kans zorg belangrijk denken elkaar groep
Topic #2:
dieren schip vluchtelingen migranten virus mens virussen boord coronavirus zegt vleermuizen dier passagiers sars europa griekse wereld nieuwe syrie haven wilde honden miljoen quarantaine syrische jaar komen pest lego eten
Topic #3:
zegt gaan kinderen elkaar afstand dag thuis zitten komen gaat meter corona houden huis uur week weken goed zit staan echt blijven komt dagen normaal ouders vertelt man tijd zien
Topic #4:
vakantie onderwijs leerlingen gaan online zegt reizen reis docenten studenten krijgen gaat zomervak

In [52]:
%%time
# LDA visualization
pyLDAvis.sklearn.prepare(lda_tf_50, dtm_tf, tf_vectorizer)

Wall time: 14min 46s


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
40    -0.116883 -0.001484       1        1  11.668668
3     -0.055830 -0.107662       2        1   7.744979
32     0.113263  0.023970       3        1   4.455153
46     0.105921 -0.032177       4        1   4.298153
14     0.134308  0.023791       5        1   4.238244
20     0.050977  0.037450       6        1   4.168843
1      0.107001 -0.013450       7        1   3.687192
15     0.021189 -0.010029       8        1   3.663384
12     0.160218 -0.021324       9        1   3.646460
45     0.109886 -0.110879      10        1   3.372503
23    -0.014194  0.175707      11        1   3.144550
37     0.061222 -0.071013      12        1   3.139766
41     0.022632 -0.126186      13        1   2.907762
35    -0.110073 -0.082672      14        1   2.600480
6     -0.062343 -0.052859      15        1   2.293606
25    -0.040364 -0.058362      16        1   2.053619
18     0.089957  0.163510      17        1   1.868837
36     0.012493  0.137369      18        1   1.741719
5      0.140896 -0.004049      19        1   1.513897
42     0.087349  0.035925      20        1   1.502352
24     0.121546  0.023488      21        1   1.474387
48    -0.138278 -0.047756      22        1   1.390263
13    -0.003367 -0.113948      23        1   1.273564
7     -0.091729  0.036164      24        1   1.249385
30    -0.171609  0.049390      25        1   1.215416
43    -0.101883 -0.037281      26        1   1.208003
8      0.103472 -0.037571      27        1   1.132859
2      0.046562  0.037752      28        1   1.099037
38     0.009653 -0.107586      29        1   1.064660
22     0.110739  0.010339      30        1   1.056886
0     -0.036814 -0.114448      31        1   1.026825
11    -0.066543  0.111015      32        1   0.979802
47    -0.021574  0.040964      33        1   0.966299
21    -0.020077  0.148724      34        1   0.965674
28     0.002048 -0.000962      35        1   0.904249
16     0.000829 -0.039677      36        1   0.899490
9      0.020340  0.061608      37        1   0.887577
27     0.093170  0.133383      38        1   0.802197
49    -0.132319 -0.006342      39        1   0.779554
17    -0.084276 -0.070236      40        1   0.772271
33    -0.006046 -0.066782      41        1   0.720270
4      0.035625 -0.163637      42        1   0.690590
19    -0.032478  0.086047      43        1   0.645686
29    -0.015035  0.088322      44        1   0.599113
44    -0.049980 -0.000335      45        1   0.561243
26    -0.055119 -0.034189      46        1   0.426887
10    -0.180303  0.124817      47        1   0.412461
39    -0.021972 -0.049047      48        1   0.411498
31    -0.046454  0.032130      49        1   0.382737
34    -0.085754  0.000078      50        1   0.290950, topic_info=      Category          Freq     Term         Total  loglift  logprob
13497  Default  24031.000000     jaar  24031.000000  30.0000  30.0000
5125   Default   5601.000000    china   5601.000000  29.0000  29.0000
8140   Default   9241.000000     euro   9241.000000  28.0000  28.0000
30207  Default  11973.000000    virus  11973.000000  27.0000  27.0000
6385   Default   4246.000000      den   4246.000000  26.0000  26.0000
...        ...           ...      ...           ...      ...      ...
13497  Topic50    113.194137     jaar  24031.565143   0.4818  -4.7784
17015  Topic50     73.258262      mei   2960.504877   2.1407  -5.2135
21067  Topic50     51.136866     paul    820.278138   3.0646  -5.5730
24267  Topic50     51.573425  seizoen   2159.134870   2.1053  -5.5645
6077   Topic50     47.682873    dagen   6297.768786   0.9564  -5.6430

[3710 rows x 6 columns], token_table=       Topic      Freq          Term
term                                
4         24  0.923065          aait
6          3  0.034932  aalderenrome
6          5  0.908240  aalderenrome
40         1  0.003596       aandeel
40         3  0.057531       aandeel
...      ...

## End of topic model part

**Below I use the outcomes of the model for further analysis**

**Select right topic model, i.e. 20 or 30**

In [56]:
# create a doc-topic matrix

path = 'P:/My documents/Corona project/'
os.chdir(path)

import numpy as np

filenames = df1['file'].values.astype('U')

dates = df1['date'].values.astype('U')

newspaper = df1['newspaper'].values.astype('U')


dtm_transformed = tf_vectorizer.fit_transform(df1['body'].values.astype('U'))

doctopic = lda_tf_50.fit_transform(dtm_transformed)

doctopic = doctopic / np.sum(doctopic, axis=1, keepdims=True)

# Write doctopic to a csv file
os.chdir(path)  

# filenamesclean = [fn.split('\\')[-1] for fn in filenames]
i=0
with open('doctopic_corona.csv',mode='w') as fo:
    for rij in doctopic:
        fo.write('"'+filenames[i]+'"')
        fo.write(',')
        fo.write('"'+dates[i]+'"')
        fo.write(',')
        fo.write('"'+newspaper[i]+'"')
        fo.write(',')
        for kolom in rij:
            fo.write(str(kolom))
            fo.write(',')
        fo.write('\n')
        i+=1
print("finsihed with creating doctopic matrix")

finsihed with creating doctopic matrix


In [57]:
dfm = pd.read_csv("P:/My documents/Corona project/doctopic_corona.csv", header=None, index_col=False,
                  names = ["file", "date", "newspaper", 
                           "t_0", "t_1","t_2", "t_3", "t_4", "t_5", "t_6", "t_7", "t_8", "t_9",
                          "t_10", "t_11", "t_12", "t_13", "t_14", "t_15", "t_16", "t_17", "t_18", "t_19",
                           "t_20", "t_21", "t_22", "t_23", "t_24", "t_25", "t_26", "t_27", "t_28", "t_29",                           
                            "t_30", "t_31", "t_32", "t_33", "t_34", "t_35", "t_36", "t_37", "t_38", "t_39",
                            "t_40", "t_41", "t_42", "t_43", "t_44", "t_45", "t_46", "t_47", "t_48", "t_49",
                          ])

dfm['datetime'] = pd.to_datetime(dfm['date'], format='%d/%m/%Y')
dfm

file        date  \
0             #coronahulp_ veel aanbod, weinig vraag.txt  14/03/2020   
1      #VeiligAchterGlas_ Portretten in tijden van is...  03/04/2020   
2      #VIRALEN Corona leidt tot andere liefdesverhal...  01/04/2020   
3                                        (Geen) hond.txt  18/03/2020   
4             (Nog niet) alle remmen los in de sport.txt  29/04/2020   
...                                                  ...         ...   
19182  Zweten in teststraat;Dik ingepakte GGD-medewer...  12/08/2020   
19183                Zweten op je hete thuiswerkplek.txt  13/08/2020   
19184                                Zweven is leven.txt  29/08/2020   
19185                                     Zwier;ikje.txt  12/06/2020   
19186                                Zwijg, Doutzen!.txt  25/07/2020   

      newspaper       t_0       t_1       t_2       t_3       t_4       t_5  \
0          volk  0.022152  0.000090  0.000090  0.516597  0.000090  0.000090   
1          volk  0.000500  0.000500  0.000500  0.000500  0.000500  0.117551   
2           nrc  0.000183  0.000183  0.000183  0.104686  0.000183  0.000183   
3          volk  0.000081  0.076914  0.241513  0.000081  0.000081  0.000081   
4          volk  0.014867  0.000039  0.000039  0.412649  0.000039  0.000039   
...         ...       ...       ...       ...       ...       ...       ...   
19182      tele  0.000056  0.000056  0.000056  0.581963  0.000056  0.000056   
19183      volk  0.000087  0.000087  0.000087  0.538137  0.000087  0.013824   
19184      volk  0.000093  0.000093  0.000093  0.000093  0.000093  0.000093   
19185       nrc  0.310211  0.000408  0.000408  0.167453  0.000408  0.000408   
19186      tele  0.000114  0.141976  0.000114  0.000114  0.000114  0.000114   

            t_6  ...      t_41      t_42      t_43      t_44      t_45  \
0      0.000090  ...  0.000090  0.000090  0.000090  0.000090  0.000090   
1      0.000500  ...  0.106508  0.000500  0.000500  0.000500  0.000500   
2      0.000183  ...  0.000183  0.000183  0.000183  0.000183  0.000183   
3      0.000081  ...  0.000081  0.000081  0.000081  0.000081  0.000081   
4      0.136885  ...  0.000039  0.000039  0.000039  0.000039  0.000039   
...         ...  ...       ...       ...       ...       ...       ...   
19182  0.000056  ...  0.000056  0.000056  0.000056  0.000056  0.000056   
19183  0.000087  ...  0.000087  0.000087  0.000087  0.032694  0.239164   
19184  0.000093  ...  0.000093  0.000093  0.000093  0.000093  0.000093   
19185  0.000408  ...  0.000408  0.000408  0.000408  0.000408  0.000408   
19186  0.000114  ...  0.000114  0.000114  0.000114  0.000114  0.000114   

           t_46      t_47      t_48      t_49   datetime  
0      0.000090  0.089511  0.021045  0.000090 2020-03-14  
1      0.000500  0.000500  0.000500  0.000500 2020-04-03  
2      0.000183  0.093834  0.000183  0.000183 2020-04-01  
3      0.000081  0.000081  0.000081  0.000081 2020-03-18  
4      0.000039  0.000039  0.000039  0.000039 2020-04-29  
...         ...       ...       ...       ...        ...  
19182  0.000056  0.000056  0.000056  0.000056 2020-08-12  
19183  0.000087  0.071868  0.000087  0.000087 2020-08-13  
19184  0.000093  0.000093  0.000093  0.000093 2020-08-29  
19185  0.000408  0.000408  0.000408  0.000408 2020-06-12  
19186  0.000114  0.044981  0.000114  0.000114 2020-07-25  

[19187 rows x 54 columns]

In [58]:
# calculate mean, std, cutoff high, and cutoff low

dfm1 = dfm.describe().loc[['mean','std']]
dfm2 = dfm1.transpose()
dfm2['cutoff_high'] = dfm2['mean'] + 2*dfm2['std'] 
dfm2['cutoff_low'] = dfm2['mean'] + dfm2['std'] 
dfm2

mean       std  cutoff_high  cutoff_low
t_0   0.011991  0.051187     0.114366    0.063179
t_1   0.031949  0.086148     0.204244    0.118097
t_2   0.010020  0.051670     0.113359    0.061689
t_3   0.068162  0.138351     0.344864    0.206513
t_4   0.007916  0.043920     0.095756    0.051836
t_5   0.024119  0.093591     0.211302    0.117711
t_6   0.029193  0.117837     0.264866    0.147030
t_7   0.010405  0.045688     0.101780    0.056092
t_8   0.011937  0.058156     0.128248    0.070092
t_9   0.009429  0.048802     0.107032    0.058231
t_10  0.005492  0.041304     0.088101    0.046797
t_11  0.009781  0.045261     0.100303    0.055042
t_12  0.032784  0.107126     0.247036    0.139910
t_13  0.012818  0.052116     0.117050    0.064934
t_14  0.044977  0.114730     0.274437    0.159707
t_15  0.030301  0.089529     0.209358    0.119829
t_16  0.008995  0.049099     0.107192    0.058094
t_17  0.009112  0.048248     0.105608    0.057360
t_18  0.016554  0.070445     0.157443    0.086999
t_19  0.007859  0.051647     0.111154    0.059506
t_20  0.038545  0.109582     0.257708    0.148126
t_21  0.009168  0.046302     0.101772    0.055470
t_22  0.011279  0.062733     0.136744    0.074011
t_23  0.025732  0.092412     0.210556    0.118144
t_24  0.013328  0.060208     0.133743    0.073535
t_25  0.021293  0.095086     0.211465    0.116379
t_26  0.005752  0.037293     0.080338    0.043045
t_27  0.008079  0.048027     0.104132    0.056105
t_28  0.010194  0.051554     0.113301    0.061748
t_29  0.006190  0.037153     0.080496    0.043343
t_30  0.013051  0.054882     0.122814    0.067932
t_31  0.005703  0.042021     0.089746    0.047725
t_32  0.039859  0.127826     0.295512    0.167686
t_33  0.011105  0.053434     0.117973    0.064539
t_34  0.003674  0.029439     0.062552    0.033113
t_35  0.026342  0.084274     0.194889    0.110616
t_36  0.013516  0.049209     0.111935    0.062726
t_37  0.028917  0.104812     0.238541    0.133729
t_38  0.013211  0.056533     0.126277    0.069744
t_39  0.005222  0.039036     0.083293    0.044257
t_40  0.086551  0.165948     0.418447    0.252499
t_41  0.031488  0.098588     0.228664    0.130076
t_42  0.015362  0.059758     0.134879    0.075120
t_43  0.012319  0.072218     0.156756    0.084538
t_44  0.005168  0.032350     0.069868    0.037518
t_45  0.038816  0.116239     0.271293    0.155055
t_46  0.068980  0.188794     0.446569    0.257775
t_47  0.010453  0.043302     0.097058    0.053756
t_48  0.015524  0.062850     0.141225    0.078374
t_49  0.011386  0.054782     0.120949    0.066167

In [ ]:
# Select the appropriate cutoff point per topic from the table above

#Topic_0 (...)
t_0_cutoff_low = dfm2.get_value('t_0', 'cutoff_low')

#Topic_1 (...)
t_1_cutoff_low = dfm2.get_value('t_1', 'cutoff_low')

#Topic_2 (...)
t_2_cutoff_low = dfm2.get_value('t_2', 'cutoff_low')

#Topic_3 (...)
t_3_cutoff_low = dfm2.get_value('t_3', 'cutoff_low')

#Topic_4 (...)
t_4_cutoff_low = dfm2.get_value('t_4', 'cutoff_low')

#Topic_5 (...)
t_5_cutoff_low = dfm2.get_value('t_5', 'cutoff_low')

#Topic_6 (...)
t_6_cutoff_low = dfm2.get_value('t_6', 'cutoff_low')

#Topic_7 (...)
t_7_cutoff_low = dfm2.get_value('t_7', 'cutoff_low')

#Topic_8 (...)
t_8_cutoff_low = dfm2.get_value('t_8', 'cutoff_low')

#Topic_9 (...)
t_9_cutoff_low = dfm2.get_value('t_9', 'cutoff_low')

#Topic_10 (...)
t_10_cutoff_low = dfm2.get_value('t_10', 'cutoff_low')

#Topic_11 (...)
t_11_cutoff_low = dfm2.get_value('t_11', 'cutoff_low')

#Topic_12 (...)
t_12_cutoff_low = dfm2.get_value('t_12', 'cutoff_low')

#Topic_13 (...)
t_13_cutoff_low = dfm2.get_value('t_13', 'cutoff_low')

#Topic_14 (...)
t_14_cutoff_low = dfm2.get_value('t_14', 'cutoff_low')

#Topic_15 (...)
t_15_cutoff_low = dfm2.get_value('t_15', 'cutoff_low')

#Topic_16 (...)
t_16_cutoff_low = dfm2.get_value('t_16', 'cutoff_low')

#Topic_17 (...)
t_17_cutoff_low = dfm2.get_value('t_17', 'cutoff_low')

#Topic_18 (...)
t_18_cutoff_low = dfm2.get_value('t_18', 'cutoff_low')

#Topic_19 (...)
t_19_cutoff_low = dfm2.get_value('t_19', 'cutoff_low')

#Topic_20 (...)
t_20_cutoff_low = dfm2.get_value('t_20', 'cutoff_low')

#Topic_21 (...)
t_21_cutoff_low = dfm2.get_value('t_21', 'cutoff_low')

#Topic_22 (...)
t_22_cutoff_low = dfm2.get_value('t_22', 'cutoff_low')

#Topic_23 (...)
t_23_cutoff_low = dfm2.get_value('t_23', 'cutoff_low')

#Topic_24 (...)
t_24_cutoff_low = dfm2.get_value('t_24', 'cutoff_low')

#Topic_25 (...)
t_25_cutoff_low = dfm2.get_value('t_25', 'cutoff_low')

#Topic_26 (...)
t_26_cutoff_low = dfm2.get_value('t_26', 'cutoff_low')

#Topic_27 (...)
t_27_cutoff_low = dfm2.get_value('t_27', 'cutoff_low')

#Topic_28 (...)
t_28_cutoff_low = dfm2.get_value('t_28', 'cutoff_low')

#Topic_29 (...)
t_29_cutoff_low = dfm2.get_value('t_29', 'cutoff_low')


In [ ]:
# These values are used to create 'low' dummies in the original df 


# dfm voor print
dfm['t_0_low'] = 0
dfm['t_0_low'][
    (dfm['t_0'] > t_0_cutoff_low)
    ] = 1 

dfm['t_1_low'] = 0
dfm['t_1_low'][
    (dfm['t_1'] > t_1_cutoff_low)
    ] = 1 

dfm['t_2_low'] = 0
dfm['t_2_low'][
    (dfm['t_2'] > t_2_cutoff_low)
    ] = 1 

dfm['t_3_low'] = 0
dfm['t_3_low'][
    (dfm['t_3'] > t_3_cutoff_low)
    ] = 1 

dfm['t_4_low'] = 0
dfm['t_4_low'][
    (dfm['t_4'] > t_4_cutoff_low)
    ] = 1 

dfm['t_5_low'] = 0
dfm['t_5_low'][
    (dfm['t_5'] > t_5_cutoff_low)
    ] = 1

dfm['t_6_low'] = 0
dfm['t_6_low'][
    (dfm['t_6'] > t_6_cutoff_low)
    ] = 1 

dfm['t_7_low'] = 0
dfm['t_7_low'][
    (dfm['t_7'] > t_7_cutoff_low)
    ] = 1 

dfm['t_8_low'] = 0
dfm['t_8_low'][
    (dfm['t_8'] > t_8_cutoff_low)
    ] = 1 

dfm['t_9_low'] = 0
dfm['t_9_low'][
    (dfm['t_9'] > t_9_cutoff_low)
    ] = 1 

dfm['t_10_low'] = 0
dfm['t_10_low'][
    (dfm['t_10'] > t_10_cutoff_low)
    ] = 1 

dfm['t_11_low'] = 0
dfm['t_11_low'][
    (dfm['t_11'] > t_11_cutoff_low)
    ] = 1 

dfm['t_12_low'] = 0
dfm['t_12_low'][
    (dfm['t_12'] > t_12_cutoff_low)
    ] = 1 

dfm['t_13_low'] = 0
dfm['t_13_low'][
    (dfm['t_13'] > t_13_cutoff_low)
    ] = 1

dfm['t_14_low'] = 0
dfm['t_14_low'][
    (dfm['t_14'] > t_14_cutoff_low)
    ] = 1 

dfm['t_15_low'] = 0
dfm['t_15_low'][
    (dfm['t_15'] > t_15_cutoff_low)
    ] = 1 

dfm['t_16_low'] = 0
dfm['t_16_low'][
    (dfm['t_16'] > t_16_cutoff_low)
    ] = 1 

dfm['t_17_low'] = 0
dfm['t_17_low'][
    (dfm['t_17'] > t_17_cutoff_low)
    ] = 1 

dfm['t_18_low'] = 0
dfm['t_18_low'][
    (dfm['t_18'] > t_18_cutoff_low)
    ] = 1 

dfm['t_19_low'] = 0
dfm['t_19_low'][
    (dfm['t_19'] > t_19_cutoff_low)
    ] = 1 

dfm['t_20_low'] = 0
dfm['t_20_low'][
    (dfm['t_20'] > t_20_cutoff_low)
    ] = 1 

dfm['t_21_low'] = 0
dfm['t_21_low'][
    (dfm['t_21'] > t_21_cutoff_low)
    ] = 1 

dfm['t_22_low'] = 0
dfm['t_22_low'][
    (dfm['t_22'] > t_22_cutoff_low)
    ] = 1 

dfm['t_23_low'] = 0
dfm['t_23_low'][
    (dfm['t_23'] > t_23_cutoff_low)
    ] = 1 

dfm['t_24_low'] = 0
dfm['t_24_low'][
    (dfm['t_24'] > t_24_cutoff_low)
    ] = 1

dfm['t_25_low'] = 0
dfm['t_25_low'][
    (dfm['t_25'] > t_25_cutoff_low)
    ] = 1 

dfm['t_26_low'] = 0
dfm['t_26_low'][
    (dfm['t_26'] > t_26_cutoff_low)
    ] = 1 

dfm['t_27_low'] = 0
dfm['t_27_low'][
    (dfm['t_27'] > t_27_cutoff_low)
    ] = 1 

dfm['t_28_low'] = 0
dfm['t_28_low'][
    (dfm['t_28'] > t_28_cutoff_low)
    ] = 1 

dfm['t_29_low'] = 0
dfm['t_29_low'][
    (dfm['t_29'] > t_29_cutoff_low)
    ] = 1 

dfm

**Identify top articles per topic and moving articles to new folder**

File name of original docx file is longer than file name in column 'file'. For now it takes too much time to solve this issue. Later this can be done.

**topic 4**

In [ ]:
# Newspaper articles with strong association with topic x
dfm_4 = dfm[dfm.t_4_low != 0]
dfm_4 = dfm_4[['file', 'datetime', 'newspaper', 't_4']]
print(dfm_4.shape)
# Write list to Excel file
os.chdir(path)
writer = pd.ExcelWriter('top_t_4.xlsx', engine='xlsxwriter')
dfm_4.to_excel(writer, sheet_name='Sheet1')
writer.save()
print(dfm_4.shape)

# Copy the subcorpus from its original folder to a new destination folder
import shutil
import os
# Create A folder for dance articles, if the folder does not exists.
if not os.path.exists('P:/My documents/Corona project/t_4'):
    os.makedirs('P:/My documents/Corona project/t_4')  
CORPUS_PATH_SELECTION = 'P:/My documents/Corona project/t_4'

os.chdir(corpus_path)

# the following list of articles are dance articles:
files_tocopy = dfm_4['file'].values.astype('U')
for f in files_tocopy:
    shutil.copy(f, CORPUS_PATH_SELECTION)      
print ("Done with copying files")    

**Number of articles per topic per day (for graphing)**

In [ ]:
# Week data

# t_4
g4 = dfm.set_index('datetime').resample('W')['t_4_low'].sum()
g4 = g4.reset_index()


In [ ]:
# Merge data frames 
# 4, 6, 7, 12, 13, 14, 16, 22, 24

dfs = [g4, g6, g7, g13, g14, g15, g18, g22, g24, g27]
from functools import reduce
df_topic_week = reduce(lambda  left,right: pd.merge(left,right,on=['datetime'],
                                            how='left'), dfs)
df_topic_week

In [ ]:
df_topic_week = df_topic_week.drop(df_topic_week.index[21])

In [ ]:
# day data
# t_4
g4 = dfm.set_index('datetime').resample('D')['t_4_low'].sum()
g4 = g4.reset_index()


In [ ]:
# Merge data frames 
# 4, 6, 7, 12, 13, 14, 16, 22, 24

dfs = [g4, g6, g7, g13, g14, g15, g18, g22, g24, g27]
from functools import reduce
df_topic_day = reduce(lambda  left,right: pd.merge(left,right,on=['datetime'],
                                            how='left'), dfs)
df_topic_day

In [ ]:
# Week data 
# Topics 0, 1
# DUAL AXIS
# https://plot.ly/python/text-and-annotations/
import plotly.graph_objects as go
from plotly.subplots import make_subplots

x = df_topic_week['datetime']

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])


fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_4_low'], name="Topic 4 (start en verspreiding virus)", opacity=0.7, line=dict(color='#FA824C', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_6_low'], name="Topic 6 (overheidsmaatregelen)", opacity=0.7, line=dict(color='#A6B1E1', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_7_low'], name="Topic 7 (omgang gezondheidsrisico's)", opacity=0.7, line=dict(color='#B4869F', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_13_low'], name="Topic 13 (virus verspreiding/overdracht)", opacity=0.7, line=dict(color='#4E4C67', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_14_low'], name="Topic 14 (ziekenhuis/IC bedden)", opacity=0.7, line=dict(color='#AFA2FF', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_15_low'], name="Topic 15 (lokale effecten)", opacity=0.7, line=dict(color='#985F6F', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_18_low'], name="Topic 18 (bedrijven/overheidssteun)", opacity=0.7, line=dict(color='#636B61', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_22_low'], name="Topic 22 (buitenland/reizen)", opacity=0.7, line=dict(color='#72788D', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_24_low'], name="Topic 24 (familie/human interest)", opacity=0.7, line=dict(color='#E3D7FF', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_week['t_27_low'], name="Topic 27 (musea/evenementen)", opacity=0.7, line=dict(color='#FF5D73', width=2)),
    secondary_y=False)




fig.update_layout(showlegend=True,
    xaxis_rangeslider_visible=True,
    width=1200,
    height=600,
    title_text='Verschillende topics in het Nederlandse nieuws over COVID-19 (week data)',
    annotations=[
            dict(
            x="2019-12-31",
            y=0,         
            text="China raporteerd eerste patienten met onbekend virus aan WHO",
            ax=-90,
            ay=-290,
            opacity=0.5,
            arrowhead=7),
            
            dict(
            x="2020-02-27",
            y=0,         
            text="Eerste corona patient in Nederland",
            ax=-90,
            ay=-270,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-09",
            y=0,         
            text="Pers conf: geen handen schudden",
            ax=-90,
            ay=-250,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-15",
            y=0,         
            text="Press conf: scholen en horeca sluiten",
            ax=-90,
            ay=-230,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-16",
            y=0,         
            text="Televisie toespraak Rutte",
            ax=-90,
            ay=-210,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-04-01",
            y=0,         
            text="Motie Asscher en Wilders over IC bedden",
            ax=-350,
            ay=-190,
            opacity=0.5,
            arrowhead=7),
    
    
            dict(
            x="2020-04-21",
            y=0,         
            text="Pers conf: deel scholen weer open, geen evenementen tot 1 september",
            ax=-350,
            ay=-170,
            opacity=0.5,
            arrowhead=7),
    
    ])

fig.update_layout(paper_bgcolor='rgba(0,0,0,0)', plot_bgcolor='rgba(0,0,0,0)')
fig.update_xaxes(title_text="Date", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(title_text="# Articles", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
# fig.update_yaxes(title_text="# References to Econony and hospital", showgrid=False, secondary_y=True)
fig.show()

In [ ]:
# Save figure
import chart_studio
username = 'renswilderom' # your username
api_key = 'JQ0okV7QsrTwEJJfp7dp' # your api key - go to profile > settings > regenerate key
chart_studio.tools.set_credentials_file(username=username, api_key=api_key)
import chart_studio.plotly as py
py.plot(fig, filename = 'Various topics in Dutch news on COVID-19 (weekly data)', auto_open=True)
import plotly.io as pio
pio.write_html(fig, file='Various topics in Dutch news on COVID-19 (weekly data)', auto_open=True)

In [ ]:
# day data 
# Topics 0, 1
# DUAL AXIS
# https://plot.ly/python/text-and-annotations/
import plotly.graph_objects as go
from plotly.subplots import make_subplots

x = df_topic_day['datetime']

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])


fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_4_low'], name="Topic 4 (start en verspreiding virus)", opacity=0.7, line=dict(color='#FA824C', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_6_low'], name="Topic 6 (overheidsmaatregelen)", opacity=0.7, line=dict(color='#A6B1E1', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_7_low'], name="Topic 7 (omgang gezondheidsrisico's)", opacity=0.7, line=dict(color='#B4869F', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_13_low'], name="Topic 13 (virus verspreiding/overdracht)", opacity=0.7, line=dict(color='#4E4C67', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_14_low'], name="Topic 14 (ziekenhuis/IC bedden)", opacity=0.7, line=dict(color='#AFA2FF', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_15_low'], name="Topic 15 (lokale effecten)", opacity=0.7, line=dict(color='#985F6F', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_18_low'], name="Topic 18 (bedrijven/overheidssteun)", opacity=0.7, line=dict(color='#636B61', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_22_low'], name="Topic 22 (buitenland/reizen)", opacity=0.7, line=dict(color='#72788D', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_24_low'], name="Topic 24 (familie/human interest)", opacity=0.7, line=dict(color='#E3D7FF', width=2)),
    secondary_y=False)

fig.add_trace(
    go.Scatter(x=x, y=df_topic_day['t_27_low'], name="Topic 27 (musea/evenementen)", opacity=0.7, line=dict(color='#FF5D73', width=2)),
    secondary_y=False)




fig.update_layout(showlegend=True,
    xaxis_rangeslider_visible=True,
    width=1200,
    height=600,
    title_text='Various topics in Dutch news on COVID-19 (daily data)',
    annotations=[
            dict(
            x="2019-12-31",
            y=0,         
            text="China raporteerd eerste patienten met onbekend virus aan WHO",
            ax=-90,
            ay=-290,
            opacity=0.5,
            arrowhead=7),
            
            dict(
            x="2020-02-27",
            y=0,         
            text="Eerste corona patient in Nederland",
            ax=-90,
            ay=-270,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-09",
            y=0,         
            text="Pers conf: geen handen schudden",
            ax=-90,
            ay=-250,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-15",
            y=0,         
            text="Press conf: scholen en horeca sluiten",
            ax=-90,
            ay=-230,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-03-16",
            y=0,         
            text="Televisie toespraak Rutte",
            ax=-90,
            ay=-210,
            opacity=0.5,
            arrowhead=7),
        
            dict(
            x="2020-04-01",
            y=0,         
            text="Motie Asscher en Wilders over IC bedden",
            ax=-350,
            ay=-190,
            opacity=0.5,
            arrowhead=7),
    
    
            dict(
            x="2020-04-21",
            y=0,         
            text="Pers conf: deel scholen weer open, geen evenementen tot 1 september",
            ax=-350,
            ay=-170,
            opacity=0.5,
            arrowhead=7),
    
    ])

fig.update_layout(paper_bgcolor='rgba(0,0,0,0)', plot_bgcolor='rgba(0,0,0,0)')
fig.update_xaxes(title_text="Date", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(title_text="# Articles", showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
# fig.update_yaxes(title_text="# References to Econony and hospital", showgrid=False, secondary_y=True)
fig.show()

In [ ]:
# Save figure
import chart_studio
username = 'renswilderom' # your username
api_key = 'JQ0okV7QsrTwEJJfp7dp' # your api key - go to profile > settings > regenerate key
chart_studio.tools.set_credentials_file(username=username, api_key=api_key)
import chart_studio.plotly as py
py.plot(fig, filename = 'Various topics in Dutch news on COVID-19 (daily data)', auto_open=True)
import plotly.io as pio
pio.write_html(fig, file='Various topics in Dutch news on COVID-19 (daily data)', auto_open=True)

***

## Correlations

***

In [ ]:
# Merge
df_all = pd.merge(df_temp_nan, df_topic_day, on='datetime', how='left')
df_all

In [ ]:
# # Merge angst and topics only
# df_angst_topic = pd.merge(df5, df_topic_day, on='datetime', how='left')
# df_angst_topic.rename(columns={'angst': 'Angst', 't_0_low': 'Topic 0', 't_1_low': 'Topic 1'}, inplace=True)
# df_angst_topic


In [ ]:
# see also https://plotlyblog.tumblr.com/post/174657459542/what-is-a-splom-chart-making-scatterplot-matrices

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

corrs = df_angst_topic.corr()
mask = np.zeros_like(corrs)
mask[np.triu_indices_from(mask)] = True
sns.heatmap(corrs, cmap='Spectral_r', mask=mask, square=True)
plt.title('Correlation matrix')

In [ ]:
# https://medium.com/@ozan/interactive-plots-with-plotly-and-cufflinks-on-pandas-dataframes-af6f86f62d94
#importing Pandas 
import pandas as pd
#importing plotly and cufflinks in offline mode
import cufflinks as cf
import plotly.offline
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)
df_all.corr().iplot(kind='heatmap',colorscale="Greens", title = "Feature Correlation Matrix")

### Working with time series data from John Hopkins Institute

In [ ]:
# read as df
import os
corpus_path = 'P:/My documents/Corona project'
os.chdir(corpus_path)
import pandas as pd
df = pd.read_csv("time_series_covid19_confirmed_global.csv", encoding='UTF-8')
df.reset_index(level=0, inplace=True)
print(df.shape)
df.head()

In [ ]:
df1 = df.loc[df['Country/Region'] == 'Netherlands']
df1 = df1.loc[df1['Long'] == 5.2913] # Focus on NL only, and not former colonies
df1 = df1.drop(df1.columns[[0, 1, 2, 3, 4]], axis=1) # drop columns 
df1 = df1.unstack().reset_index() # from wide to long
df1 = df1.drop(df1.columns[[1]], axis=1) # drop column 
df1.rename(columns={'level_0': 'date', 0: 'confirmed'}, inplace=True) # rename
df1['datetime']  = pd.to_datetime(df1['date']) # to datetime
df1

In [ ]:
df1.drop(df1.loc[df1['datetime'] > '2020-03-31 00:00:00'].index, inplace=True)
df1

In [ ]:
# https://plot.ly/python/line-charts/
df_melt = df1.melt(id_vars='datetime', value_vars=['confirmed'])

import plotly.graph_objects as go
fig = go.Figure()


# Create and style traces
fig.add_trace(go.Scatter(x=df_melt['datetime'], y=df_melt['value'], name='# Confirmed Covid-19 patients',
                         line=dict(color='pink', width=2)))


# Edit the layout
fig.update_layout(title="Number of confirmed Covid-19 patients in the Netherlands (John Hopkins Institute Data)",
                    showlegend=False,
                    xaxis_rangeslider_visible=True,
                   xaxis_title='Date',
                   yaxis_title='# Confirmed Covid-19 patients',
                   paper_bgcolor='rgba(0,0,0,0)',
                   plot_bgcolor='rgba(0,0,0,0)')

fig.update_xaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')
fig.update_yaxes(showgrid=True, gridwidth=0.3, gridcolor='LightGrey')


fig.show() # 'svg' helps to share graph through nbviewer. If this is not necessary, it can be removed for a better interactive plot.
